In [36]:
# scrape presidential speeches for text about oil

import requests
from bs4 import BeautifulSoup
import re
import os
from selenium import webdriver
import time

url = 'https://millercenter.org/the-presidency/presidential-speeches'

In [30]:
oil_words = ['oil', 'petroleum', 'OPEC', 'crude', 'gasoline', 'gas', 'fuel', 'energy', 'drilling', 'pipeline', 'refinery', 'barrel', 'barrels', 'platform', 'offshore', 'onshore']
climate_words = ['climate', 'Paris', 'sustainable', 'green', 'carbon', 'emission', 'renewable', 'solar', 'wind', 'hydro', 'geothermal', 'nuclear', 'clean', 'pollution', 'sustainability', 'environment', 'ecology', 'conservation', 'recycle', 'recycling', 'renewal']

In [38]:
# get html from url
html = ''
for i in range(10):
    response = requests.get(url + '?page=' + str(i))
    html += response.text

# parse html
soup = BeautifulSoup(html, 'html.parser')

# get all links to presidential speeches and let it load

speech_links = []
for a in soup.find_all('a', href=True):
    if '/the-presidency/presidential-speeches/' in a['href']:
        speech_links.append(a['href'])
        
speech_links = list(set(speech_links))

In [40]:
# get text from each speech

texts = []

for link in speech_links:
    response = requests.get(link)
    html = response.content
    soup = BeautifulSoup(html, 'html.parser')
    text = soup.get_text()
    text = text.replace('\n', ' ')
    text = text.replace('\r', ' ')
    text = text.replace('\t', ' ')
    texts.append(text)

print(texts[3])

Exception ignored in: <finalize object at 0x1135ea5a0; dead>
Traceback (most recent call last):
  File "/Users/jeudi/anaconda3/lib/python3.11/weakref.py", line 590, in __call__
    return info.func(*info.args, **(info.kwargs or {}))
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/jeudi/anaconda3/lib/python3.11/site-packages/urllib3/connectionpool.py", line 1130, in _close_pool_connections
    conn.close()
  File "/Users/jeudi/anaconda3/lib/python3.11/http/client.py", line 964, in close
    sock.close()   # close it manually... there may be other refs
    ^^^^^^^^^^^^
  File "/Users/jeudi/anaconda3/lib/python3.11/socket.py", line 503, in close
    self._real_close()
  File "/Users/jeudi/anaconda3/lib/python3.11/ssl.py", line 1337, in _real_close
    super()._real_close()
  File "/Users/jeudi/anaconda3/lib/python3.11/socket.py", line 497, in _real_close
    _ss.close(self)
KeyboardInterrupt: 


KeyboardInterrupt: 

In [42]:
len(texts)

305

In [80]:
def find_third_occurrence_index(text, phrase):
    # Find all occurrences of the phrase
    occurrences = [m.start() for m in re.finditer(phrase, text)]
    
    # Check if there are at least three occurrences
    if len(occurrences) < 3:
        return "Phrase not found three times in the text"
    
    # Get the index of the third occurrence
    third_occurrence_index = occurrences[2]
    
    return third_occurrence_index

In [56]:
def count_phrase_occurrences(text, phrase):
    # Use re.findall to find all occurrences of the phrase
    occurrences = re.findall(phrase, text)
    
    # Return the total number of occurrences
    return len(occurrences)

In [82]:
# find the date and speaker of each speech

text_dict = {i: {'text': texts[i]} for i in range(len(texts))}
for i in range(len(texts)):
    text = texts[i]
    # date is from 41 until the first ':'
    start = 41
    end = text.find(':')
    date = text[start:end]
    if date:
        text_dict[i]['date'] = date
    else:
        text_dict[i]['date'] = 'unknown'
text_dict

# 'About this speech' + 'Presidential Speeches'

{0: {'text': '                                         June 9, 1982: Address to the Bundestag in West Germany | Miller Center               Skip to main content                       Main navigation  The Presidency   U.S. Presidents   George Washington John Adams Thomas Jefferson James Madison James Monroe John Quincy Adams Andrew Jackson Martin Van Buren William Harrison John Tyler James K. Polk Zachary Taylor Millard Fillmore Franklin Pierce James Buchanan Abraham Lincoln Andrew Johnson Ulysses S. Grant Rutherford B. Hayes James A. Garfield Chester A. Arthur Grover Cleveland Benjamin Harrison William McKinley Theodore Roosevelt William Taft Woodrow Wilson Warren G. Harding Calvin Coolidge Herbert Hoover Franklin D. Roosevelt Harry S. Truman Dwight D. Eisenhower John F. Kennedy Lyndon B. Johnson Richard Nixon Gerald Ford Jimmy Carter Ronald Reagan George H. W. Bush Bill Clinton George W. Bush Barack Obama Donald Trump Joe Biden    Presidential Speeches Presidential Oral Histories Secr

In [86]:
# parse out texts after 'View Transcript            Transcript' and before 'View Transcript'

for i in range(len(texts)):
    # find first and second appearences of 'View Transcript'
    text = text_dict[i]['text']
    start = text.find('View Transcript')
    end = text.find('View Transcript', start+1)
    edited_text = text[start:end][38:-3]
    if start > 0 and end > 0:
        text_dict[i]['edited_text'] = edited_text
    else:
        text_dict[i]['edited_text'] = 'unknown'

text_dict[45]['edited_text']

'THE PRESIDENT: Thank you, Paul and Mitch, for the introduction and for your tremendous leadership. You folks have done well. I just looked at some numbers. You’ve even done better than you thought, I think—(laughter)—based on what we just saw about 10 minutes ago. And I want to thank you, to the Governor of this incredible state, my very good friend, Jim Justice and his wonderful wife, Cathy, who are with us. And Jim is now a proud member of the Republican Party. He was a Democrat. He switched over, right? (Applause.) You don’t see that too often. Maybe we’ll see it more and more. But thank you, Jim. And the hotel is beautiful, and everything is beautiful. We appreciate it. It’s great to be among so many friends for the second time this week. Tuesday was an incredible evening, as we were all inspired. (Applause.) And I really mean that. We were inspired by America’s heroes and uplifted by everyone who has sacrificed in the fight for freedom. They were, and are, incredible people that 

In [87]:
# find all sentences containing oil words
for i in range(len(texts)):
    oil_sentences = []
    text = text_dict[i]['edited_text']
    for sentence in re.split(r'(?<!\w\.\w.)(?<![A-Z][a-z]\.)(?<=\.|\?)\s', text):
        for word in oil_words:
            if word in sentence:
                oil_sentences.append(sentence)
    text_dict[i]['oil_sentences'] = oil_sentences

In [88]:
# find all sentences containing climate words

climate_sentences = []

for i in range(len(texts)):
    climate_sentences = []
    text = text_dict[i]['edited_text']
    for sentence in re.split(r'(?<!\w\.\w.)(?<![A-Z][a-z]\.)(?<=\.|\?)\s', text):
        for word in climate_words:
            if word in sentence:
                climate_sentences.append(sentence)
    text_dict[i]['climate_sentences'] = climate_sentences

In [89]:
# get the number of sentences containing oil words and climate words
for i in range(len(texts)):
    text_dict[i]['oil_sentence_count'] = len(text_dict[i]['oil_sentences'])
    text_dict[i]['climate_sentence_count'] = len(text_dict[i]['climate_sentences'])

In [90]:
import pandas as pd
df = pd.DataFrame(text_dict).T

In [92]:
# change date to datetime

df['date'] = pd.to_datetime(df['date'])
df.head()

text       date  \
0                                           June ... 1982-06-09   
1                                           March... 2022-03-01   
2                                           Septe... 1983-09-05   
3                                           March... 2020-03-13   
4                                           Janua... 1991-01-16   

                                         edited_text  \
0  Mr. President, Chancellor Schmidt, members of ...   
1  SPEAKER OF THE HOUSE NANCY PELOSI: Members of ...   
2  My fellow Americans: I'm coming before you ton...   
3  THE PRESIDENT: Thank you very much, everyone. ...   
4  Just 2 hours ago, allied air forces began an a...   

                                       oil_sentences  \
0  [It is as stark as that gash of a border that ...   
1  [ Tonight, I can announce that the United Stat...   
2  [Memories come back of Czechoslovakia, Hungary...   
3  [He immediately called the private sector labo...   
4  [A world in which brutality and lawlessness ar...   

                                   climate_sentences oil_sentence_count  \
0  [Our method has been to organize our defensive...                  3   
1  [ And we’ll do it all to withstand the devasta...                 13   
2  [Ambassador Nitze has returned to Geneva to re...                  2   
3  [Walgreens., CORNELL: Well, Mr. President, tha...                  9   
4  [We are determined to knock out Saddam Hussein...                  1   

  climate_sentence_count  
0                     14  
1                      7  
2                      1  
3                      6  
4                      2

In [95]:
# save to csv
df.to_csv('presidential_speeches.csv', index=False)